# Exploring measurement

(Srikumar K. S., 15 Apr 2023)

The goal of this exploratory notebook is to examine measurement as a process of
interaction between a high dimensional system and a qubit being measured.

In [23]:
using Random, LinearAlgebra
rng = MersenneTwister(1234)

MersenneTwister(1234)


$$
\newcommand{\ket}[1]{\left|{#1}\right\rangle}
\newcommand{\bra}[1]{\left\langle{#1}\right|}
\newcommand{\braket}[1]{\left\langle{#1}\right\rangle}
$$


## Approach

The idea is to see how a qubit in a random superposition of its two possibilities evolves when "measured" by a random observer that can distinguish between the two qubit states. Towards this, we need the ability to construct a random state, a random observable and a random observer. In this exploration, we're not initially concerned with the nature of the distribution when creating random states/observables and observers. We'll get to that later on ... if necessary.

## Random states

We can make any N-dimensional random vector with complex components such that $\sum_{i}|c_i|^2 = 1$ where $c_i$ are the amplitudes of the basis states that make up the random state vector. Note that the constraint implies $|c_i|^2 \leq 1$ for all $i$.

In [24]:
function random_state(rng, N)
    @assert N >= 2
    z = zeros(Complex, N)
    for i in 1:N
        a = 2.0 * (rand(rng, Float64) - 0.5)
        b = 2.0 * (rand(rng, Float64) - 0.5)
        z[i] = a+b*im
    end
    return z / sqrt(sum(abs2, z))
end

random_state(rng, 4)

4-element Vector{ComplexF64}:
 0.13894291414503196 + 0.4080544353672953im
 0.10130724069115052 - 0.06104772848254118im
 0.44969950485897653 + 0.5416517697082908im
 -0.4579406055551145 - 0.30801068114907093im

## Random density matrix

A random density matrix must meet the criterion that its eigenvalues must be real and they must sum to unity.

In [25]:

function random_ρ(rng, N; noise_floor=1e-10/N, bias=ones(Float64,N))
    m = 2.0 * (rand(rng, Float64, (N,N)) + im * rand(rng, Float64, (N,N)) .- (0.5 + im*0.5))
    m = 0.5*(m+m')
    e = eigen(m)
    eva = abs2.(e.values)
    evam = maximum(eva)
    ev = (eva .+ noise_floor * evam) .* bias
    ev /= sum(ev)
    e.vectors * Diagonal(ev) * inv(e.vectors)
end

random_ρ(rng, 4)

4×4 Matrix{ComplexF64}:
  0.0981778-5.40725e-18im  …    -0.011408+0.0348368im
 -0.0607316-0.00682211im        0.0594336-0.180245im
 0.00579272-0.0772894im       -0.00395489+0.00300028im
  -0.011408-0.0348368im          0.191688+1.65149e-17im

## Random observers

What is a random observer? Let's focus on observers for single qubits. A single qubit can be either in the $\ket{0}$ state or in the $\ket{1}$ state or in general in a superposition of the form $\ket{q} = q_0\ket{0}+q_1\ket{1}$ where $|q_0|^2 + |q_1|^2 = 1$. Let's consider an "ideal observer" represented by a unitary operator $\Omega$ and with $n$ dimensional internal state $\ket{\omega}$ which behaves like this -

$$\Omega\ket{\omega}\ket{0} = \ket{\omega_0}\ket{0}$$
and
$$\Omega\ket{\omega}\ket{1} = \ket{\omega_1}\ket{1}$$

Therefore such an $\Omega$ will transform an arbitrary $\ket{q}$ according to --

$$\Omega\ket{\omega}\ket{q} = q_0\ket{\omega_0}\ket{0} + q_1\ket{\omega_1}\ket{1}$$

Such an $\Omega$ can be thought of as a combination of $\Omega_0$ and $\Omega_1$ where --

$$\Omega_0\ket{\omega}\ket{q} = q_0\ket{\omega_0}\ket{0} + q_1\ket{\omega}\ket{1}$$
and
$$\Omega_1\ket{\omega}\ket{q} = q_0\ket{\omega}\ket{0} + q_1\ket{\omega_1}\ket{1}$$

and we can write -

$$\Omega = \Omega_1\Omega_0 = \Omega_0\Omega_1$$

We can therefore pick $\Omega_0$ and $\Omega_1$ to be unitary transformations due to random commuting observables $H_0$ and $H_1$.

The combined observable (a self adjoint matrix) can therefore be written as --

$$H = \begin{bmatrix}
H_0 & \mathbb{0} \\
\mathbb{0} & H_1
\end{bmatrix}$$

In [26]:

function random_observable(rng, N; minmax=(-1.0,1.0))
    m = 2.0 * (rand(rng, Float64, (N,N)) + im * rand(rng, Float64, (N,N)) .- (0.5 + im*0.5))
    m = 0.5*(m+m')
    e = eigen(m)
    emin = minimum(real.(e.values))
    emax = maximum(real.(e.values))
    ev = minmax[1] .+ (e.values .- emin) * ((minmax[2] - minmax[1]) / (emax - emin))
    e.vectors * Diagonal(ev) * inv(e.vectors)
end

eigen(random_observable(rng, 4))

Eigen{ComplexF64, ComplexF64, Matrix{ComplexF64}, Vector{ComplexF64}}
values:
4-element Vector{ComplexF64}:
 -0.9999999999999992 + 2.865976966174497e-17im
 -0.7017467680014327 + 2.2852080636888333e-17im
 0.03676648290639895 + 3.66067959963041e-17im
  1.0000000000000004 + 3.2140735975966996e-17im
vectors:
4×4 Matrix{ComplexF64}:
 0.645644+0.0im        -0.140488+0.620761im  …   -0.144119-0.257587im
 0.134682+0.435929im    0.666776+0.0im           -0.133027-0.275052im
 0.288964+0.0572762im   0.313974-0.137567im       0.830699+0.0im
 0.535022+0.0440478im  -0.144123-0.109784im     -0.0465203+0.356796im

In [27]:

function random_observer(rng, n; minmax=(-1.0,1.0))
    H0 = random_observable(rng, n; minmax)
    H1 = random_observable(rng, n; minmax)
    Z = zeros(Complex, (n,n))
    H = vcat(hcat(H0, Z), hcat(Z, H1))
end

random_observer(rng, 2)

4×4 Matrix{Complex}:
  0.623319+0.0im       -0.239081-0.744522im    …          0+0im
 -0.239081+0.744522im  -0.623319+6.1382e-18im             0+0im
         0+0im                 0+0im              -0.479245+0.812471im
         0+0im                 0+0im              -0.331987-6.7288e-17im

## Utilities

We need some utilities like ability to make pure state vectors, take scalar products, tensor products and such.

In [28]:

function pure_state(N, m)
    z = zeros(Complex, N)
    m = mod(m, N)
    z[m+1] = 1.0 + 0im
    return z
end

function bra(state)
    state'
end

function braket(state1, state2)
    bra(state1) * state2
end

function ketbra(state1, state2)
    state1 * bra(state2)
end

function ρ(probs)
    aprobs = abs.(probs)
    nprobs = aprobs / sum(aprobs)
    return Diagonal{Complex,Vector{Complex}}(nprobs)
end

# The purity of the state represented by a sensity matrix is
# the trace of its square. The purity will be 1 if it represents
# a pure state and less than 1 if the state is a mixed state.
function purity(density)
    tr(density * density)
end

# We extend that notion of purity of a density matrix to that
# of a state, relative of the chosen set of basis states as well.
# Straightforward extension ... and I'm not even sure I'll be using it.
function spurity(state)
    s = state .* conj.(state)
    sum(abs2, s)
end

# Tensor product of states is just the kron operator.
⊗ = kron

# Exepectation of an operator given the density matrix.
function E(densityop, op)
    tr(densityop * op)
end

# Pauli matrices and identity matrices.
σx = Complex.([0 1; 1 0])
σy = Complex.([0 (-im); (im) 0])
σz = Complex.([1 0; 0 -1])
Ik(k) = Diagonal(ones(Complex, k))
I = Ik(2)

# Pauli rotation. Computes e^{iPa}
# Assumes that pauli * pauli = I, i.e. pauli is its own inverse.
function rot(pauli, alpha)
    id = Ik(size(pauli)[1])
    cos(alpha) * id + im * sin(alpha) * pauli
end

rot (generic function with 1 method)

In [29]:
display(pure_state(2,0))
display(Ik(4))
display(rot(kron(σx,I), pi/5))

2-element Vector{Complex}:
 1.0 + 0.0im
   0 + 0im

4×4 Diagonal{Complex, Vector{Complex}}:
 1+0im    ⋅      ⋅      ⋅  
   ⋅    1+0im    ⋅      ⋅  
   ⋅      ⋅    1+0im    ⋅  
   ⋅      ⋅      ⋅    1+0im

4×4 Matrix{ComplexF64}:
 0.809017+0.0im            0.0+0.0im       …       0.0+0.0im
      0.0+0.0im       0.809017+0.0im               0.0+0.587785im
      0.0+0.587785im       0.0+0.0im               0.0+0.0im
      0.0+0.0im            0.0+0.587785im     0.809017+0.0im

## Evolution due to a random observable

We take a random observable $H$ and evolve a random state $\ket{r}$ over time
using the unitary operation $\ket{r(t)} = e^{i2\pi Ht}\ket{r}$. Then we compare the result state to the
original random state as a function of time using the dot product of the two
states $\braket{r(t)|r}$. We use $2\pi$ as a convenience so the H makes sense as a spectrum.

In [30]:
function random_evolution(rng, n, T, dt)
    H = random_observable(rng, n)
    r = random_state(rng, n)
    r0 = r
    evolve = exp(im * 2 * pi * dt * H)
    result = []
    for t in 0:dt:T
        push!(result, braket(r, r0))
        r = evolve * r
    end
    
    return real.(result), imag.(result)
end

using Plots
p = plot(random_evolution(rng, 4, 100, 0.01)[1])
savefig(p, "state-evolution.svg")

"/Users/sriku/Downloads/state-evolution.svg"

That is kind of what you'd expect - a superposition of oscillations at a number of different frequencies.

## Using an observer

Now what happens to the states if we evolve a random state similarly using an
observer. We'll try to look at the observation process as a series of small unitary
transformations and keep track of how the two states of the original measured qubit
evolve when considered along with the n states of the observer.

In [31]:
function evolve_observer(rng, n, T, dt)
    H = random_observer(rng, n)
    w = random_state(rng, n)
    q = random_state(rng, 2)
    r = kron(q,w)
    r0 = r
    result = []
    evolve = exp(im * 2 * pi * H * dt)
    for t in 0:dt:T
        costate_0 = r[1:n]
        costate_1 = r[n+1:end]
        costate_0 /= sqrt(sum(abs2, costate_0))
        costate_1 /= sqrt(sum(abs2, costate_1))
        push!(result, braket(costate_0, costate_1))
        r = evolve * r
    end
    return abs.(result)
end

evols = evolve_observer.(rng, 2 .^ (4:8), 10, 0.1)
p = plot(evols)
savefig(p, "evolve-observer.svg")


"/Users/sriku/Downloads/evolve-observer.svg"

That looks interesting to me. While initially there is some correlation between the two parts of the
state vector $r_{1\ldots n}$ and $r_{(n+1)\ldots 2n}$, it rapidly declines to near 0 and lingers around 0 forever, the larger $n$ gets. For small $n$, we essentially have a small coherent superposition, but the superpositions get complex for observers with larger n. Let's split the plots into a series and see it more clearly.

In [32]:
tsteps = 0:0.1:100
evols = evolve_observer.(rng, 2 .^ (4:10), tsteps[end], tsteps[2]-tsteps[1])
p = plot(tsteps, [evols...], layout=(length(evols),1), size=(500,1000))
savefig(p, "evolve-observer-stack.svg")

"/Users/sriku/Downloads/evolve-observer-stack.svg"

Let's now zoom in to the first few "seconds" to see what happens there.

In [33]:
zoom=1:30
p = plot(tsteps[zoom], [e[zoom] for e in evols], layout=(length(evols),1), size=(500,1000))
savefig(p, "decoherence-process.svg")

"/Users/sriku/Downloads/decoherence-process.svg"

## Observations

The dot products of the two co-states goes to zero after about a time of $1$
for larger $n$.

The dot product of the co-states represents the internal states taken on by the
observer for each of the two states of the qubit - i.e. the
two possibilities starting with $\ket{\omega}\ket{0}$ and
$\ket{\omega}\ket{1}$.

I interpret the dot product of the co-states going to 0 as $n$ becomes larger,
as the states evolving in their own "worlds" and not crossing each other.
If they did cross, it would mean that at some point in the future of the
observer the qubit and the observer would become separable.

## Analysis

Given the observer $H = \begin{bmatrix} H_0 & 0 \\ 0 & H_1 \end{bmatrix}$, and $H_0$ and $H_1$ are both self adjoint (i.e. $H_0 = H_0^\dagger$ and $H_1 = H_1^\dagger$), we have --

$$ e^{iHt} = \begin{bmatrix} e^{iH_0t} & 0 \\ 0 & e^{iH_1t} \end{bmatrix} $$

If we notate the combined state vector of the observer+qubit system as $\ket{\Psi} = \ket{q} \otimes \ket{psi} = \begin{bmatrix}q_0\ket{\psi} \\ q_1\ket{\psi}\end{bmatrix}$ where $\ket{q} = q_0\ket{0} + q_1\ket{1}$ (implying $|q_0|^2 + |q_1|^2 = 1$), The evolution of the joint state can be written --

$$e^{iHt}\ket{\Psi} = \begin{bmatrix}q_0e^{iH_0t}\ket{\psi} \\ q_1e^{iH_1t}\ket{\psi}\end{bmatrix} = \begin{bmatrix} q_0\ket{\psi_0(t)} \\ q_1\ket{\psi_1(t)}\end{bmatrix}$$

So if we're examining the inner product of the two co-state vectors, we get -

$$ \alpha = \braket{\psi\left|e^{-iH_1t}e^{iH_0t}\right|\psi} = \braket{\psi\left|e^{i(H_0-H_1)t}\right|\psi} = \braket{\psi\left|e^{i\Delta Ht}\right|\psi}$$ 

If $H_0$ and $H_1$ are very close to each other, then $\Delta H$ ends up being small -- i.e. its eigenvalues end up small relative to the eigenvalues of $H_0$ and $H_1$ and the inner product becomes close to $1.0$. Therefore for $H$ to actually represent an observer, it must be able to differentiate between the two qubit states and therefore $\Delta H$ itself must have random eigen values comparable in magnitude to both $H_0$ and $H_1$. 

If we then consider $\ket{\psi}$ in an eigen basis $\ket{\phi_k}$ of $\Delta H$ with $\braket{\phi_i|\phi_j} = \delta_{ij}$ and $\Delta H \ket{\phi_k} = 2\pi f_k\ket{\phi_k}$, then taking $\ket{\psi} = \sum_k{\beta_k\ket{\phi_k}}$, we see that -

$$ \alpha = \sum_k{|\beta_k|^2e^{i(2\pi f_kt)}} $$

So if a) $\ket{\psi}$ is mixed enough in that basis and b) the "frequencies" $f_k$ are different enough, then for $t \gtrapprox 0$, we see that $\alpha \approx 1$ and as $t$ increases, all sorts of frequencies will get mixed up and $\alpha \to 0$ with larger dimensions $n \gg 1$. So the behaviour of the observer relative to the qubit states must also not have degenerate eigenvalues, or at least have sufficient number of different eigenvalues ("frequencies"). If we start out in a pure state of the observer system in that eigen basis though, we'll get $\alpha = 1$. The interval during which $\alpha \sim 1$ (say $\alpha > 0.5$) can then be called the "coherence interval" of the observer, beyond which you get "decoherence".

So this is what we're seeing in the trend plot in the previous section using a random observer starting out at a random state.

All these points correlate well with the mental model of "observer" that I started with, so I'm wondering whether all this should've been "obvious" from the get go :)  I'm still irked by not being able to see why the Born rule has to hold based on this model of an observer, but that problem remains unsolved for now.